# CSGY 6923 Machine Learning - Final Project

# Building a BERT Model from Scratch

This notebook implements a BERT (Bidirectional Encoder Representations from Transformers) model from scratch using PyTorch. We'll train it on the WikiText dataset for two tasks:
1. Masked Language Modeling (MLM)
2. Next Sentence Prediction (NSP)


Installing huggingface and pytorch specific dependencies

In [ ]:
!pip install datasets transformers==4.18.0 sentencepiece
!pip install torchtext==0.18.0

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.3/70.3 kB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.0/4.0 MB 63.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 43.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 13.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 21.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 14.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.6/6.6 MB 92.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 897.5/897.5 kB 62.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 21.5 MB/s eta 0:00:00
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.20.3
    Uninstalling tokenizers-0.20.3:
      Successfully uninstalled tokenizers-0.20.3
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024

## Setting Up the Environment

Import all necessary modules and mount Google Drive to store our vocabulary and model weights.

In [ ]:
from datasets import *
import argparse
from torch.utils.data import DataLoader
from torch.utils.data import Dataset
import torch.nn as nn
import torch.nn.functional as F
from torch.optim import Adam
from torch.utils.data import DataLoader
import torch
import math
import numpy as np
import tqdm
import random
import pickle
from collections import Counter
from typing import Dict, List, Tuple, Optional
import re
import nltk
from tqdm.notebook import tqdm as notebook_tqdm

# Connect with Google Drive
from google.colab import drive
drive.mount('/content/drive', force_remount = True)

nltk.download('punkt_tab')

Mounted at /content/drive


In [ ]:
cd /content/drive/My\ Drive/Colab\ Notebooks/

/content/drive/My Drive/Colab Notebooks


In [ ]:
pwd

'/content/drive/My Drive/Colab Notebooks'

In [ ]:
nltk.download('punkt')
from nltk.tokenize import sent_tokenize

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


## Building the BERT Architecture

### Attention Mechanism
The core of BERT is the transformer architecture, which relies heavily on attention mechanisms:
1. Basic Attention computation
2. Multi-Head Attention
3. Layer Normalization

The following code implements the scaled dot-product attention and multi-head attention mechanisms.

In [ ]:
class Attention(nn.Module):

    def forward(self, query, key, value, mask=None, dropout=None):
        scores = torch.matmul(query, key.transpose(-2, -1)) \
                 / math.sqrt(query.size(-1))

        if mask is not None:
            scores = scores.masked_fill(mask == 0, -1e9)

        p_attn = F.softmax(scores, dim=-1)

        if dropout is not None:
            p_attn = dropout(p_attn)

        return torch.matmul(p_attn, value), p_attn

In [ ]:
class MultiHeadedAttention(nn.Module):

    def __init__(self, h, d_model, dropout=0.1):
        super().__init__()
        assert d_model % h == 0

        # We assume d_v always equals d_k
        self.d_k = d_model // h
        self.h = h

        self.linear_layers = nn.ModuleList([nn.Linear(d_model, d_model) for _ in range(3)])
        self.output_linear = nn.Linear(d_model, d_model)
        self.attention = Attention()

        self.dropout = nn.Dropout(p=dropout)

    def forward(self, query, key, value, mask=None):
        batch_size = query.size(0)

        # 1) Do all the linear projections in batch from d_model => h x d_k
        query, key, value = [l(x).view(batch_size, -1, self.h, self.d_k).transpose(1, 2)
                             for l, x in zip(self.linear_layers, (query, key, value))]

        # 2) Apply attention on all the projected vectors in batch.
        x, attn = self.attention(query, key, value, mask=mask, dropout=self.dropout)

        # 3) "Concat" using a view and apply a final linear.
        x = x.transpose(1, 2).contiguous().view(batch_size, -1, self.h * self.d_k)

        return self.output_linear(x)

### Layer Normalization and Feed Forward Components

Implemenitng the
1. Layer normalization
2. Sublayer connection
3. Position-wise feed-forward networks with GELU activation

In [ ]:
class LayerNorm(nn.Module):

    def __init__(self, features, eps=1e-6):
        super(LayerNorm, self).__init__()
        self.a_2 = nn.Parameter(torch.ones(features))
        self.b_2 = nn.Parameter(torch.zeros(features))
        self.eps = eps

    def forward(self, x):
        mean = x.mean(-1, keepdim=True)
        std = x.std(-1, keepdim=True)
        return self.a_2 * (x - mean) / (std + self.eps) + self.b_2

In [ ]:
class SublayerConnection(nn.Module):

    def __init__(self, size, dropout):
        super(SublayerConnection, self).__init__()
        self.norm = LayerNorm(size)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x, sublayer):
        return x + self.dropout(sublayer(self.norm(x)))

In [ ]:
class GELU(nn.Module):

    def forward(self, x):
        return 0.5 * x * (1 + torch.tanh(math.sqrt(2 / math.pi) * (x + 0.044715 * torch.pow(x, 3))))

In [ ]:
class PositionwiseFeedForward(nn.Module):

    def __init__(self, d_model, d_ff, dropout=0.1):
        super(PositionwiseFeedForward, self).__init__()
        self.w_1 = nn.Linear(d_model, d_ff)
        self.w_2 = nn.Linear(d_ff, d_model)
        self.dropout = nn.Dropout(dropout)
        self.activation = GELU()

    def forward(self, x):
        return self.w_2(self.dropout(self.activation(self.w_1(x))))

### BERT's Core Components

Now we'll implement the main BERT components:
1. Transformer blocks
2. Embedding layers (Token, Position, and Segment embeddings)
3. The main BERT model
4. Task-specific heads (MLM and NSP)

In [ ]:
class TransformerBlock(nn.Module):

    def __init__(self, hidden, attn_heads, feed_forward_hidden, dropout):

        super().__init__()
        self.attention = MultiHeadedAttention(h=attn_heads, d_model=hidden)
        self.feed_forward = PositionwiseFeedForward(d_model=hidden, d_ff=feed_forward_hidden, dropout=dropout)
        self.input_sublayer = SublayerConnection(size=hidden, dropout=dropout)
        self.output_sublayer = SublayerConnection(size=hidden, dropout=dropout)
        self.dropout = nn.Dropout(p=dropout)

    def forward(self, x, mask):
        x = self.input_sublayer(x, lambda _x: self.attention.forward(_x, _x, _x, mask=mask))
        x = self.output_sublayer(x, self.feed_forward)
        return self.dropout(x)

In [ ]:
class TokenEmbedding(nn.Embedding):
    def __init__(self, vocab_size, embed_size=512):
        super().__init__(vocab_size, embed_size, padding_idx=0)

In [ ]:
class PositionalEmbedding(nn.Module):

    def __init__(self, d_model, max_len=512):
        super().__init__()

        # Compute the positional encodings once in log space.
        pe = torch.zeros(max_len, d_model).float()
        pe.require_grad = False

        position = torch.arange(0, max_len).float().unsqueeze(1)
        div_term = (torch.arange(0, d_model, 2).float() * -(math.log(10000.0) / d_model)).exp()

        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)

        pe = pe.unsqueeze(0)
        self.register_buffer('pe', pe)

    def forward(self, x):
        return self.pe[:, :x.size(1)]

In [ ]:
class SegmentEmbedding(nn.Embedding):
    def __init__(self, embed_size=512):
        super().__init__(3, embed_size, padding_idx=0)

In [ ]:
class BERTEmbedding(nn.Module):
    def __init__(self, vocab_size, embed_size, dropout=0.1):
        super().__init__()
        self.token = TokenEmbedding(vocab_size=vocab_size, embed_size=embed_size)
        self.position = PositionalEmbedding(d_model=self.token.embedding_dim)
        self.segment = SegmentEmbedding(embed_size=self.token.embedding_dim)
        self.dropout = nn.Dropout(p=dropout)
        self.embed_size = embed_size

    def forward(self, sequence, segment_label):
        x = self.token(sequence) + self.position(sequence) + self.segment(segment_label)
        return self.dropout(x)

### The Complete BERT Model

Combining all parts of the model for MLM and NSP (Masked LM and Next Sentence Prediction)

In [ ]:
class BERT(nn.Module):

    def __init__(self, vocab_size, hidden=768, n_layers=12, attn_heads=12, dropout=0.1):

        super().__init__()
        self.hidden = hidden
        self.n_layers = n_layers
        self.attn_heads = attn_heads

        # paper noted they used 4*hidden_size for ff_network_hidden_size
        self.feed_forward_hidden = hidden * 4

        # embedding for BERT, sum of positional, segment, token embeddings
        self.embedding = BERTEmbedding(vocab_size=vocab_size, embed_size=hidden)

        # multi-layers transformer blocks, deep network
        self.transformer_blocks = nn.ModuleList(
            [TransformerBlock(hidden, attn_heads, hidden * 4, dropout) for _ in range(n_layers)])

    def forward(self, x, segment_info):
        # attention masking for padded token
        # torch.ByteTensor([batch_size, 1, seq_len, seq_len)
        mask = (x > 0).unsqueeze(1).repeat(1, x.size(1), 1).unsqueeze(1)

        # embedding the indexed sequence to sequence of vectors
        x = self.embedding(x, segment_info)

        # running over multiple transformer blocks
        for transformer in self.transformer_blocks:
            x = transformer.forward(x, mask)

        return x

In [ ]:
class BERTLM(nn.Module):
    """
    BERT Language Model
    Next Sentence Prediction Model + Masked Language Model
    """

    def __init__(self, bert: BERT, vocab_size):
        """
        :param bert: BERT model which should be trained
        :param vocab_size: total vocab size for masked_lm
        """

        super().__init__()
        self.bert = bert
        self.next_sentence = NextSentencePrediction(self.bert.hidden)
        self.mask_lm = MaskedLanguageModel(self.bert.hidden, vocab_size)

    def forward(self, x, segment_label):
        x = self.bert(x, segment_label)
        return self.next_sentence(x), self.mask_lm(x)


class NextSentencePrediction(nn.Module):
    """
    2-class classification model : is_next, is_not_next
    """

    def __init__(self, hidden):
        """
        :param hidden: BERT model output size
        """
        super().__init__()
        self.linear = nn.Linear(hidden, 2)
        self.softmax = nn.LogSoftmax(dim=-1)

    def forward(self, x):
        return self.softmax(self.linear(x[:, 0]))


class MaskedLanguageModel(nn.Module):
    """
    predicting origin token from masked input sequence
    n-class classification problem, n-class = vocab_size
    """

    def __init__(self, hidden, vocab_size):
        """
        :param hidden: output size of BERT model
        :param vocab_size: total vocab size
        """
        super().__init__()
        self.linear = nn.Linear(hidden, vocab_size)
        self.softmax = nn.LogSoftmax(dim=-1)

    def forward(self, x):
        return self.softmax(self.linear(x))

## Training the model

### Optimizer and Learning Rate Scheduling

We implement a custom learning rate scheduler that follows the original BERT paper's approach with warmup steps and decay.

In [ ]:
class ScheduledOptim:

    def __init__(self, optimizer, d_model, n_warmup_steps):
        self._optimizer = optimizer
        self.n_warmup_steps = n_warmup_steps
        self.n_current_steps = 0
        self.init_lr = np.power(d_model, -0.5)

    def step_and_update_lr(self):
        "Step with the inner optimizer"
        self._update_learning_rate()
        self._optimizer.step()

    def zero_grad(self):
        "Zero out the gradients by the inner optimizer"
        self._optimizer.zero_grad()

    def _get_lr_scale(self):
        return np.min([
            np.power(self.n_current_steps, -0.5),
            np.power(self.n_warmup_steps, -1.5) * self.n_current_steps])

    def _update_learning_rate(self):
        ''' Learning rate scheduling per step '''

        self.n_current_steps += 1
        lr = self.init_lr * self._get_lr_scale()

        for param_group in self._optimizer.param_groups:
            param_group['lr'] = lr

### Training and Evaluation

The following classes handle the training loop and data management:
1. `BERTTrainer`: Manages the training process
2. `BERTDataset`: Handles data preprocessing and loading

In [ ]:
class BERTTrainer:

    def __init__(self, bert: BERT, vocab_size: int,
                 train_dataloader: DataLoader, test_dataloader: DataLoader = None,
                 lr: float = 1e-4, betas=(0.9, 0.999), weight_decay: float = 0.01, warmup_steps=10000,
                 with_cuda: bool = True, cuda_devices=None, log_freq: int = 10):

        # Setup cuda device for BERT training, argument -c, --cuda should be true
        cuda_condition = torch.cuda.is_available() and with_cuda
        self.device = torch.device("cuda:0" if cuda_condition else "cpu")

        # This BERT model will be saved every epoch
        self.bert = bert
        # Initialize the BERT Language Model, with BERT model
        self.model = BERTLM(bert, vocab_size).to(self.device)

        # Distributed GPU training if CUDA can detect more than 1 GPU
        if with_cuda and torch.cuda.device_count() > 1:
            print("Using %d GPUS for BERT" % torch.cuda.device_count())
            self.model = nn.DataParallel(self.model, device_ids=cuda_devices)

        # Setting the train and test data loader
        self.train_data = train_dataloader
        self.test_data = test_dataloader

        # Setting the Adam optimizer with hyper-param
        self.optim = Adam(self.model.parameters(), lr=lr, betas=betas, weight_decay=weight_decay)
        self.optim_schedule = ScheduledOptim(self.optim, self.bert.hidden, n_warmup_steps=warmup_steps)

        # Using Negative Log Likelihood Loss function for predicting the masked_token
        self.criterion = nn.NLLLoss(ignore_index=0)

        self.log_freq = log_freq

        print("Total Parameters:", sum([p.nelement() for p in self.model.parameters()]))

    def train(self, epoch):
        self.iteration(epoch, self.train_data)

    def test(self, epoch):
        self.iteration(epoch, self.test_data, train=False)

    def iteration(self, epoch, data_loader, train=True):
        """
        loop over the data_loader for training or testing
        if on train status, backward operation is activated
        and also auto save the model every peoch
        :param epoch: current epoch index
        :param data_loader: torch.utils.data.DataLoader for iteration
        :param train: boolean value of is train or test
        :return: None
        """
        str_code = "train" if train else "test"

        # Setting the tqdm progress bar
        data_iter = tqdm.tqdm(enumerate(data_loader),
                              desc="EP_%s:%d" % (str_code, epoch),
                              total=len(data_loader),
                              bar_format="{l_bar}{r_bar}")

        avg_loss = 0.0
        total_correct = 0
        total_element = 0

        for i, data in data_iter:
            # 0. batch_data will be sent into the device(GPU or cpu)
            data = {key: value.to(self.device) for key, value in data.items()}

            # 1. forward the next_sentence_prediction and masked_lm model
            next_sent_output, mask_lm_output = self.model.forward(data["bert_input"], data["segment_label"])

            # 2-1. NLL(negative log likelihood) loss of is_next classification result
            next_loss = self.criterion(next_sent_output, data["is_next"])

            # 2-2. NLLLoss of predicting masked token word
            mask_loss = self.criterion(mask_lm_output.transpose(1, 2), data["bert_label"])

            # 2-3. Adding next_loss and mask_loss : 3.4 Pre-training Procedure
            loss = next_loss + mask_loss

            # 3. backward and optimization only in train
            if train:
                self.optim_schedule.zero_grad()
                loss.backward()
                self.optim_schedule.step_and_update_lr()

            # next sentence prediction accuracy
            correct = next_sent_output.argmax(dim=-1).eq(data["is_next"]).sum().item()
            avg_loss += loss.item()
            total_correct += correct
            total_element += data["is_next"].nelement()

            post_fix = {
                "epoch": epoch,
                "iter": i,
                "avg_loss": avg_loss / (i + 1),
                "avg_acc": total_correct / total_element * 100,
                "loss": loss.item()
            }

            if i % self.log_freq == 0:
                data_iter.write(str(post_fix))

        print("EP%d_%s, avg_loss=" % (epoch, str_code), avg_loss / len(data_iter), "total_acc=",
              total_correct * 100.0 / total_element)

    def save(self, epoch, file_path="output/bert_trained.model"):
        """
        Saving the current BERT model on file_path
        :param epoch: current epoch number
        :param file_path: model output path which gonna be file_path+"ep%d" % epoch
        :return: final_output_path
        """
        output_path = file_path + ".ep%d" % epoch
        torch.save(self.bert.cpu(), output_path)
        self.bert.to(self.device)
        print("EP:%d Model Saved on:" % epoch, output_path)
        return output_path

In [ ]:
class BERTWikiTextTrainer:
    """
    Trainer class specifically designed for BERT pretraining on WikiText data.
    Handles the training loop, optimization, and logging.
    """
    def __init__(self,
                 bert_model: nn.Module,
                 vocab_size: int,
                 train_dataloader: DataLoader,
                 valid_dataloader: Optional[DataLoader] = None,
                 lr: float = 1e-4,
                 betas: tuple = (0.9, 0.999),
                 weight_decay: float = 0.01,
                 warmup_steps: int = 10000,
                 device: Optional[str] = None,
                 log_freq: int = 10):
        """
        Initialize the trainer with model and training parameters.

        Args:
            bert_model: The BERT model to train
            vocab_size: Size of the vocabulary
            train_dataloader: DataLoader for training data
            valid_dataloader: Optional DataLoader for validation data
            lr: Learning rate
            betas: Adam optimizer betas
            weight_decay: Weight decay for optimization
            warmup_steps: Number of warmup steps for learning rate scheduling
            device: Device to train on ('cuda' or 'cpu')
            log_freq: How often to log training metrics
        """
        # Setup device
        self.device = device if device else ('cuda' if torch.cuda.is_available() else 'cpu')
        print(f"Using device: {self.device}")

        # Initialize model
        self.bert = bert_model
        self.model = BERTLM(bert_model, vocab_size).to(self.device)

        # Setup multi-GPU if available
        if self.device == 'cuda' and torch.cuda.device_count() > 1:
            print(f"Using {torch.cuda.device_count()} GPUs for training")
            self.model = nn.DataParallel(self.model)

        # Store data loaders
        self.train_dataloader = train_dataloader
        self.valid_dataloader = valid_dataloader

        # Setup optimizer with learning rate scheduling
        self.optimizer = Adam(self.model.parameters(), lr=lr, betas=betas, weight_decay=weight_decay)
        self.optim_schedule = ScheduledOptim(self.optimizer, self.bert.hidden, warmup_steps)

        # Loss function for both MLM and NSP tasks
        self.criterion = nn.NLLLoss(ignore_index=0)  # ignore padding index

        self.log_freq = log_freq
        print(f"Total Parameters: {sum([p.nelement() for p in self.model.parameters()])}")

    def train(self, epochs: int, save_path: str):
        """
        Train the model for specified number of epochs.

        Args:
            epochs: Number of epochs to train
            save_path: Where to save model checkpoints
        """
        best_loss = float('inf')

        for epoch in range(epochs):
            # Training phase
            train_stats = self.run_epoch(epoch, is_training=True)
            print(f"\nEpoch {epoch} Training Stats:")
            self._print_stats(train_stats)

            # Validation phase
            if self.valid_dataloader:
                with torch.no_grad():
                    valid_stats = self.run_epoch(epoch, is_training=False)
                print(f"\nEpoch {epoch} Validation Stats:")
                self._print_stats(valid_stats)

                # Save best model
                if valid_stats['avg_loss'] < best_loss:
                    best_loss = valid_stats['avg_loss']
                    self.save(save_path, epoch)
                    print(f"New best model saved with validation loss: {best_loss:.4f}")
            else:
                # If no validation set, save based on training loss
                self.save(save_path, epoch)

    def run_epoch(self, epoch: int, is_training: bool) -> Dict[str, float]:
        """
        Run one epoch of training or validation.

        Args:
            epoch: Current epoch number
            is_training: Whether this is a training or validation pass

        Returns:
            Dictionary containing epoch statistics
        """
        mode = "train" if is_training else "valid"
        data_loader = self.train_dataloader if is_training else self.valid_dataloader

        # Set model mode
        self.model.train() if is_training else self.model.eval()

        # Initialize statistics
        stats = {
            'total_loss': 0.0,
            'mlm_loss': 0.0,
            'nsp_loss': 0.0,
            'correct_nsp': 0,
            'total_nsp': 0
        }

        # Progress bar
        data_iter = tqdm.tqdm(
            enumerate(data_loader),
            desc=f"EP_{mode}:{epoch}",
            total=len(data_loader),
            bar_format="{l_bar}{r_bar}"
        )

        for i, data in data_iter:
            # Move data to device
            data = {key: value.to(self.device) for key, value in data.items()}

            # Forward pass
            next_sent_output, mask_lm_output = self.model.forward(
                data["bert_input"],
                data["segment_label"]
            )

            # Calculate losses
            next_loss = self.criterion(next_sent_output, data["is_next"])
            mask_loss = self.criterion(
                mask_lm_output.transpose(1, 2),
                data["bert_label"]
            )
            loss = next_loss + mask_loss

            if is_training:
                # Backward pass and optimization
                self.optim_schedule.zero_grad()
                loss.backward()
                self.optim_schedule.step_and_update_lr()

            # Update statistics
            stats['total_loss'] += loss.item()
            stats['mlm_loss'] += mask_loss.item()
            stats['nsp_loss'] += next_loss.item()
            stats['correct_nsp'] += next_sent_output.argmax(dim=-1).eq(data["is_next"]).sum().item()
            stats['total_nsp'] += data["is_next"].nelement()

            # Log progress
            if i % self.log_freq == 0:
                current_stats = {
                    'avg_loss': stats['total_loss'] / (i + 1),
                    'nsp_acc': stats['correct_nsp'] / stats['total_nsp'] * 100,
                    'lr': self.optim_schedule._optimizer.param_groups[0]['lr']
                }
                data_iter.write(
                    f"Step: {i}, Loss: {current_stats['avg_loss']:.4f}, "
                    f"NSP Acc: {current_stats['nsp_acc']:.2f}%, "
                    f"LR: {current_stats['lr']:.6f}"
                )

        # Calculate final statistics
        num_steps = len(data_loader)
        return {
            'avg_loss': stats['total_loss'] / num_steps,
            'avg_mlm_loss': stats['mlm_loss'] / num_steps,
            'avg_nsp_loss': stats['nsp_loss'] / num_steps,
            'nsp_accuracy': stats['correct_nsp'] / stats['total_nsp'] * 100
        }

    def _print_stats(self, stats: Dict[str, float]):
        """Print training/validation statistics in a formatted way."""
        print(f"  Average Loss: {stats['avg_loss']:.4f}")
        print(f"  MLM Loss: {stats['avg_mlm_loss']:.4f}")
        print(f"  NSP Loss: {stats['avg_nsp_loss']:.4f}")
        print(f"  NSP Accuracy: {stats['nsp_accuracy']:.2f}%")

    def save(self, path: str, epoch: int):
        """Save model checkpoint."""
        torch.save({
            'epoch': epoch,
            'model_state_dict': self.bert.state_dict(),
            'optimizer_state_dict': self.optimizer.state_dict(),
            'scheduler_state_dict': self.optim_schedule.state_dict()
        }, f"{path}_epoch_{epoch}.pt")


In [ ]:
class BERTDataset(Dataset):
    def __init__(self, corpus_path, vocab, seq_len, encoding="utf-8", corpus_lines=None, on_memory=True):
        self.vocab = vocab
        self.seq_len = seq_len

        self.on_memory = on_memory
        self.corpus_lines = corpus_lines
        self.corpus_path = corpus_path
        self.encoding = encoding

        with open(corpus_path, "r", encoding=encoding) as f:
            if self.corpus_lines is None and not on_memory:
                for _ in tqdm.tqdm(f, desc="Loading Dataset", total=corpus_lines):
                    self.corpus_lines += 1

            if on_memory:
                self.lines = [line[:-1].split("\t")
                              for line in tqdm.tqdm(f, desc="Loading Dataset", total=corpus_lines)]
                self.corpus_lines = len(self.lines)

        if not on_memory:
            self.file = open(corpus_path, "r", encoding=encoding)
            self.random_file = open(corpus_path, "r", encoding=encoding)

            for _ in range(random.randint(self.corpus_lines if self.corpus_lines < 1000 else 1000)):
                self.random_file.__next__()

    def __len__(self):
        return self.corpus_lines

    def __getitem__(self, item):
        t1, t2, is_next_label = self.random_sent(item)
        t1_random, t1_label = self.random_word(t1)
        t2_random, t2_label = self.random_word(t2)

        # [CLS] tag = SOS tag, [SEP] tag = EOS tag
        t1 = [self.vocab.sos_index] + t1_random + [self.vocab.eos_index]
        t2 = t2_random + [self.vocab.eos_index]

        t1_label = [self.vocab.pad_index] + t1_label + [self.vocab.pad_index]
        t2_label = t2_label + [self.vocab.pad_index]

        segment_label = ([1 for _ in range(len(t1))] + [2 for _ in range(len(t2))])[:self.seq_len]
        bert_input = (t1 + t2)[:self.seq_len]
        bert_label = (t1_label + t2_label)[:self.seq_len]

        padding = [self.vocab.pad_index for _ in range(self.seq_len - len(bert_input))]
        bert_input.extend(padding), bert_label.extend(padding), segment_label.extend(padding)

        output = {"bert_input": bert_input,
                  "bert_label": bert_label,
                  "segment_label": segment_label,
                  "is_next": is_next_label}

        return {key: torch.tensor(value) for key, value in output.items()}

    def random_word(self, sentence):
        tokens = sentence.split()
        output_label = []

        for i, token in enumerate(tokens):
            prob = random.random()
            if prob < 0.15:
                prob /= 0.15

                # 80% randomly change token to mask token
                if prob < 0.8:
                    tokens[i] = self.vocab.mask_index

                # 10% randomly change token to random token
                elif prob < 0.9:
                    tokens[i] = random.randrange(len(self.vocab))

                # 10% randomly change token to current token
                else:
                    tokens[i] = self.vocab.stoi.get(token, self.vocab.unk_index)

                output_label.append(self.vocab.stoi.get(token, self.vocab.unk_index))

            else:
                tokens[i] = self.vocab.stoi.get(token, self.vocab.unk_index)
                output_label.append(0)

        return tokens, output_label

    def random_sent(self, index):
        t1, t2 = self.get_corpus_line(index)

        # output_text, label(isNotNext:0, isNext:1)
        if random.random() > 0.5:
            return t1, t2, 1
        else:
            return t1, self.get_random_line(), 0

    def get_corpus_line(self, item):
        if self.on_memory:
            return self.lines[item][0], self.lines[item][1]
        else:
            line = self.file.__next__()
            if line is None:
                self.file.close()
                self.file = open(self.corpus_path, "r", encoding=self.encoding)
                line = self.file.__next__()

            t1, t2 = line[:-1].split("\t")
            return t1, t2

    def get_random_line(self):
        if self.on_memory:
            return self.lines[random.randrange(len(self.lines))][1]

        line = self.file.__next__()
        if line is None:
            self.file.close()
            self.file = open(self.corpus_path, "r", encoding=self.encoding)
            for _ in range(random.randint(self.corpus_lines if self.corpus_lines < 1000 else 1000)):
                self.random_file.__next__()
            line = self.random_file.__next__()
        return line[:-1].split("\t")[1]

## Vocabulary Management

We implement vocabulary handling with special token support and methods for converting between tokens and indices.

In [ ]:
class TorchVocab(object):

    def __init__(self, counter, max_size=None, min_freq=1, specials=['<pad>', '<oov>'],
                 vectors=None, unk_init=None, vectors_cache=None):

        self.freqs = counter
        counter = counter.copy()
        min_freq = max(min_freq, 1)

        self.itos = list(specials)
        # frequencies of special tokens are not counted when building vocabulary
        # in frequency order
        for tok in specials:
            del counter[tok]

        max_size = None if max_size is None else max_size + len(self.itos)

        # sort by frequency, then alphabetically
        words_and_frequencies = sorted(counter.items(), key=lambda tup: tup[0])
        words_and_frequencies.sort(key=lambda tup: tup[1], reverse=True)

        for word, freq in words_and_frequencies:
            if freq < min_freq or len(self.itos) == max_size:
                break
            self.itos.append(word)

        # stoi is simply a reverse dict for itos
        self.stoi = {tok: i for i, tok in enumerate(self.itos)}

        self.vectors = None
        if vectors is not None:
            self.load_vectors(vectors, unk_init=unk_init, cache=vectors_cache)
        else:
            assert unk_init is None and vectors_cache is None

    def __eq__(self, other):
        if self.freqs != other.freqs:
            return False
        if self.stoi != other.stoi:
            return False
        if self.itos != other.itos:
            return False
        if self.vectors != other.vectors:
            return False
        return True

    def __len__(self):
        return len(self.itos)

    def vocab_rerank(self):
        self.stoi = {word: i for i, word in enumerate(self.itos)}

    def extend(self, v, sort=False):
        words = sorted(v.itos) if sort else v.itos
        for w in words:
            if w not in self.stoi:
                self.itos.append(w)
                self.stoi[w] = len(self.itos) - 1


class Vocab(TorchVocab):
    def __init__(self, counter, max_size=None, min_freq=1):
        self.pad_index = 0
        self.unk_index = 1
        self.eos_index = 2
        self.sos_index = 3
        self.mask_index = 4
        super().__init__(counter, specials=["<pad>", "<unk>", "<eos>", "<sos>", "<mask>"],
                         max_size=max_size, min_freq=min_freq)

    def to_seq(self, sentece, seq_len, with_eos=False, with_sos=False) -> list:
        pass

    def from_seq(self, seq, join=False, with_pad=False):
        pass

    @staticmethod
    def load_vocab(vocab_path: str) -> 'Vocab':
        with open(vocab_path, "rb") as f:
            return pickle.load(f)

    def save_vocab(self, vocab_path):
        with open(vocab_path, "wb") as f:
            pickle.dump(self, f)


# Building Vocab with text files
class WordVocab(Vocab):
    def __init__(self, texts, max_size=None, min_freq=1):
        print("Building Vocab")
        counter = Counter()
        for line in tqdm.tqdm(texts):
            if isinstance(line, list):
                words = line
            else:
                words = line.replace("\n", "").replace("\t", "").split()

            for word in words:
                counter[word] += 1
        super().__init__(counter, max_size=max_size, min_freq=min_freq)

    def to_seq(self, sentence, seq_len=None, with_eos=False, with_sos=False, with_len=False):
        if isinstance(sentence, str):
            sentence = sentence.split()

        seq = [self.stoi.get(word, self.unk_index) for word in sentence]

        if with_eos:
            seq += [self.eos_index]  # this would be index 1
        if with_sos:
            seq = [self.sos_index] + seq

        origin_seq_len = len(seq)

        if seq_len is None:
            pass
        elif len(seq) <= seq_len:
            seq += [self.pad_index for _ in range(seq_len - len(seq))]
        else:
            seq = seq[:seq_len]

        return (seq, origin_seq_len) if with_len else seq

    def from_seq(self, seq, join=False, with_pad=False):
        words = [self.itos[idx]
                 if idx < len(self.itos)
                 else "<%d>" % idx
                 for idx in seq
                 if not with_pad or idx != self.pad_index]

        return " ".join(words) if join else words

    @staticmethod
    def load_vocab(vocab_path: str) -> 'WordVocab':
        with open(vocab_path, "rb") as f:
            return pickle.load(f)


def build(corpus_path: str, output_path: str, vocab_size=None, encoding: str = "utf-8",
          min_freq: int=1):

    with open(corpus_path, "r", encoding=encoding) as f:
        vocab = WordVocab(f, max_size=vocab_size, min_freq=min_freq)

    print("VOCAB SIZE:", len(vocab))
    vocab.save_vocab(output_path)

In [ ]:
pwd

'/content/drive/My Drive/Colab Notebooks'

In [ ]:
build("corpus.small", "./vocab_train.txt")

Building Vocab


120000it [00:02, 46247.97it/s]


VOCAB SIZE: 244514


## Helper functions for training

1. `train_small_bert`: scaled down to train in a few hours
2. `train_bert_wikitext`: For full-scale training

In [ ]:
def train_small_bert(epochs: int=10):
    # Direct configuration setup
    config = {
        # Required parameters
        'train_dataset': '/content/drive/MyDrive/Colab Notebooks/corpus.small',
        'vocab_path': './vocab_train.txt',
        'output_path': '/content/drive/MyDrive/Colab Notebooks/bert.model',
        'test_dataset': None,

        # Model parameters
        'hidden': 256,
        'layers': 8,
        'attn_heads': 8,
        'seq_len': 20,

        # Training parameters
        'batch_size': 64,
        'epochs': epochs,
        'num_workers': 10,

        # Runtime parameters
        'with_cuda': True,
        'log_freq': 10,
        'corpus_lines': None,
        'cuda_devices': None,
        'on_memory': True,

        # Optimizer parameters
        'lr': 1e-3,
        'adam_weight_decay': 0.01,
        'adam_beta1': 0.9,
        'adam_beta2': 0.999
    }

    print("Loading Vocab", config['vocab_path'])
    vocab = WordVocab.load_vocab(config['vocab_path'])
    print("Vocab Size: ", len(vocab))

    print("Loading Train Dataset", config['train_dataset'])
    train_dataset = BERTDataset(config['train_dataset'], vocab, seq_len=config['seq_len'],
                              corpus_lines=config['corpus_lines'], on_memory=config['on_memory'])

    print("Loading Test Dataset", config['test_dataset'])
    test_dataset = BERTDataset(config['test_dataset'], vocab, seq_len=config['seq_len'],
                              on_memory=config['on_memory']) if config['test_dataset'] else None

    print("Creating Dataloader")
    train_data_loader = DataLoader(train_dataset, batch_size=config['batch_size'],
                                  num_workers=config['num_workers'])
    test_data_loader = DataLoader(test_dataset, batch_size=config['batch_size'],
                                num_workers=config['num_workers']) if test_dataset else None

    print("Building BERT model")
    bert = BERT(len(vocab), hidden=config['hidden'], n_layers=config['layers'],
                attn_heads=config['attn_heads'])

    print("Creating BERT Trainer")
    trainer = BERTTrainer(bert, len(vocab), train_dataloader=train_data_loader,
                        test_dataloader=test_data_loader, lr=config['lr'],
                        betas=(config['adam_beta1'], config['adam_beta2']),
                        weight_decay=config['adam_weight_decay'],
                        with_cuda=config['with_cuda'], cuda_devices=config['cuda_devices'],
                        log_freq=config['log_freq'])

    print("Training Start")
    for epoch in range(config['epochs']):
        trainer.train(epoch)
        trainer.save(epoch, config['output_path'])

        if test_data_loader:
            trainer.test(epoch)


In [ ]:
train_small_bert()

## Model Inference.

Since the small BERT model has been trained (through the notebook). Let us now perform inference on some sample data to see how the model performs.

In [ ]:
def load_vocab(vocab_path):
    with open(vocab_path, "rb") as f:
        vocab = pickle.load(f)
    return vocab


def load_bert_model(model_path, device='cuda' if torch.cuda.is_available() else 'cpu'):
    """
    Load the saved BERT model
    """
    model = torch.load(model_path, map_location=device)
    model.eval()  # Set to evaluation mode
    return model


# Load the vocabulary
vocab = load_vocab("vocab_train.txt")
model = load_bert_model("bert.model.ep9")

# Create a tokenization function
def tokenize_text(text, vocab, seq_len=20):
    """
    Convert input text to tokens using the vocabulary
    Args:
        text (str): Input text
        vocab: Vocabulary object
        seq_len (int): Maximum sequence length
    Returns:
        tuple: (token_ids, segment_ids)
    """
    # Split text into tokens
    tokens = text.split()

    # Convert tokens to ids
    token_ids = [vocab.stoi.get(token, vocab.unk_index) for token in tokens]

    # Add [CLS] at start and [SEP] at end
    token_ids = [vocab.sos_index] + token_ids + [vocab.eos_index]

    # Pad or truncate to seq_len
    if len(token_ids) < seq_len:
        token_ids = token_ids + [vocab.pad_index] * (seq_len - len(token_ids))
    else:
        token_ids = token_ids[:seq_len]

    # Create segment ids (all 1's for single sequence)
    segment_ids = [1] * seq_len

    return torch.tensor([token_ids]), torch.tensor([segment_ids])

# Create inference function
def get_bert_embeddings(model, text, vocab, seq_len=20, device='cuda' if torch.cuda.is_available() else 'cpu'):
    """
    Get BERT embeddings for input text
    Args:
        model: BERT model
        text (str): Input text
        vocab: Vocabulary object
        seq_len (int): Maximum sequence length
        device (str): Device to run inference on
    Returns:
        torch.Tensor: BERT embeddings
    """
    model.eval()
    model = model.to(device)

    # Tokenize input text
    token_ids, segment_ids = tokenize_text(text, vocab, seq_len)

    # Move tensors to device
    token_ids = token_ids.to(device)
    segment_ids = segment_ids.to(device)

    # Get embeddings
    with torch.no_grad():
        embeddings = model(token_ids, segment_ids)

    return embeddings

# Let's test it with a sample sentence
test_text = "this is a test sentence"
embeddings = get_bert_embeddings(model, test_text, vocab)
print(f"Shape of embeddings: {embeddings.shape}")

<ipython-input-28-5e5a162a8ddc>:11: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model = torch.load(model_path, map_location=device)


Shape of embeddings: torch.Size([1, 20, 256])


In [ ]:
class NextSentencePrediction(nn.Module):
    def __init__(self, hidden):
        super().__init__()
        self.linear = nn.Linear(hidden, 2)
        self.softmax = nn.LogSoftmax(dim=-1)

    def forward(self, x):
        return self.softmax(self.linear(x[:, 0]))

def predict_next_sentence(model, sentence1, sentence2, vocab, seq_len=20, device='cuda' if torch.cuda.is_available() else 'cpu'):
    """
    Predict if sentence2 follows sentence1
    """
    # Combine sentences with [SEP] token
    combined_text = sentence1 + " [SEP] " + sentence2

    # Get BERT embeddings
    embeddings = get_bert_embeddings(model, combined_text, vocab, seq_len=seq_len, device=device)

    # Use NSP head to get prediction
    nsp_head = NextSentencePrediction(model.hidden).to(device)
    prediction = nsp_head(embeddings)

    # Get probabilities
    probs = torch.exp(prediction)
    return probs[0][1].item()  # Probability that sentence2 follows sentence1



def test_next_sentence_prediction():
    # Sample sentence pairs
    pairs = [
        ("the cat sat on the mat", "it was taking a nap"),
        ("the cat sat on the mat", "dogs love to play fetch"),
        ("it is raining outside", "I need an umbrella"),
        ("it is raining outside", "the cat likes milk")
    ]

    print("\nNext Sentence Prediction:")
    for sent1, sent2 in pairs:
        prob = predict_next_sentence(model, sent1, sent2, vocab)
        print(f"\nSentence 1: {sent1}")
        print(f"Sentence 2: {sent2}")
        print(f"Probability that sentence 2 follows sentence 1: {prob}")

print("\nTesting Next Sentence Prediction...")
test_next_sentence_prediction()


Testing Next Sentence Prediction...

Next Sentence Prediction:

Sentence 1: the cat sat on the mat
Sentence 2: it was taking a nap
Probability that sentence 2 follows sentence 1: 0.9739370942115784

Sentence 1: the cat sat on the mat
Sentence 2: dogs love to play fetch
Probability that sentence 2 follows sentence 1: 0.051843009889125824

Sentence 1: it is raining outside
Sentence 2: I need an umbrella
Probability that sentence 2 follows sentence 1: 0.9872457385063171

Sentence 1: it is raining outside
Sentence 2: the cat likes milk
Probability that sentence 2 follows sentence 1: 0.09107743948698044


## Training on the WikiText Dataset

We load the Salesforce/WikiText dataset from huggingface, and preprocess it to have tab separators for next sentence predictions.

In [ ]:
def clean_wikitext(text):
    """Clean WikiText formatting"""
    # Remove section headers
    if text.startswith('='):
        return ''

    # Remove article titles and other formatting
    text = re.sub(r'@-@', '-', text)  # Fix hyphenation
    text = re.sub(r'\( Japanese : .+?\)', '', text)  # Remove Japanese translations
    text = re.sub(r'\s+', ' ', text)  # Normalize whitespace
    text = re.sub(r' , ', ', ', text)  # Fix spacing around punctuation
    text = re.sub(r' \. ', '. ', text)

    # Remove citations and special characters
    text = re.sub(r'\[\d+\]', '', text)
    text = re.sub(r'[^\w\s.,!?-]', ' ', text)

    return text.strip()

def process_wikitext_to_pairs(output_file, split="train", max_pairs=None):
    dataset = load_dataset("Salesforce/wikitext", "wikitext-103-raw-v1", split=split)
    pairs = []

    for item in dataset:
        text = clean_wikitext(item['text'])
        if not text:
            continue

        sentences = [s.strip() for s in sent_tokenize(text)]
        sentences = [s for s in sentences if len(s) > 20]  # Filter short sentences

        for i in range(len(sentences) - 1):
            # Consecutive pairs (positive examples)
            pairs.append(f"{sentences[i]}\t{sentences[i+1]}\n")

            # Random pairs (negative examples)
            if random.random() < 0.5 and len(sentences) > 2:
                random_idx = random.choice([j for j in range(len(sentences)) if j != i and j != i+1])
                pairs.append(f"{sentences[i]}\t{sentences[random_idx]}\n")

        if max_pairs and len(pairs) >= max_pairs:
            break

    # Write pairs to file
    with open(output_file, 'w', encoding='utf-8') as f:
        f.writelines(pairs[:max_pairs] if max_pairs else pairs)

    return len(pairs)

In [ ]:
process_wikitext_to_pairs("wikitext_pairs.small", split="train[:20%]")

884013

## Load the WikiText Vocabulary

Reusing the `WordVocab` class, we have

In [ ]:
with open("wikitext_pairs.small", "r", encoding="utf-8") as f:
    vocab = WordVocab(f, max_size=None, min_freq=1)

print("VOCAB SIZE:", len(vocab))
vocab.save_vocab("./wikitext_vocab.txt")

Building Vocab


884013it [00:15, 58606.58it/s]


VOCAB SIZE: 855975


In [ ]:
train_dataset = BERTDataset(corpus_path="wikitext_pairs.small",
                           vocab=vocab,
                           seq_len=20,
                           corpus_lines=None,
                           on_memory=True)

train_dataloader = DataLoader(train_dataset, batch_size=32, num_workers=2)


bert = BERT(vocab_size=len(vocab),
           hidden=256,
           n_layers=6,
           attn_heads=8)

trainer = BERTTrainer(bert=bert,
                     vocab_size=len(vocab),
                     train_dataloader=train_dataloader,
                     test_dataloader=None,
                     lr=1e-3,
                     betas=(0.9, 0.999),
                     weight_decay=0.01,
                     with_cuda=True,
                     log_freq=10)

Loading Dataset: 884013it [00:02, 363331.02it/s]


Total Parameters: 443855017


In [ ]:
print("Training Start")
for epoch in range(10):  # 10 epochs
    trainer.train(epoch)
    trainer.save(epoch, "./wikitext_trained.model")

Training Start


EP_train:0:   0%|| 2/27626 [00:00<2:29:15,  3.08it/s]

{'epoch': 0, 'iter': 0, 'avg_loss': 15.758881568908691, 'avg_acc': 59.375, 'loss': 15.758881568908691}


EP_train:0:   0%|| 12/27626 [00:02<1:05:52,  6.99it/s]

{'epoch': 0, 'iter': 10, 'avg_loss': 15.898591301657937, 'avg_acc': 50.0, 'loss': 16.01879119873047}


...

EP_train:4:  55%|| 15242/27626 [36:01<29:20,  7.03it/s]

{'epoch': 4, 'iter': 15240, 'avg_loss': 8.509639276825265, 'avg_acc': 50.004510858867526, 'loss': 8.177351951599121}


EP_train:4:  55%|| 15252/27626 [36:02<29:12,  7.06it/s]

{'epoch': 4, 'iter': 15250, 'avg_loss': 8.509564730200436, 'avg_acc': 50.00102452298209, 'loss': 9.103778839111328}


EP_train:4:  55%|| 15260/27626 [36:03<29:04,  7.09it/s]